In [1]:
! pip install coloredlogs 

In [2]:
import numpy as np
import random
import math
from constants import *
import datetime as dt
from cluster_sim import Cluster
import logging
import time

logging.basicConfig(
    level=logging.DEBUG,
    format='{asctime} {levelname:<6} {message}',
    style='{'
)

2024-05-05 20:47:00 Hemadhri root[20856] INFO Initializing cluster...
2024-05-05 20:47:00 Hemadhri root[20856] INFO Cluster config: NUM_OF_NODES=3, NODE_MEMORY=1, SPAWN_TIME_INTERVAL_SECS=0.0001, MAX_NUM_OF_PODS=2399.76, ALPHA=0.3, GAMMA=0.3
2024-05-05 20:47:00 Hemadhri root[20856] INFO Run started, running for 10 seconds
2024-05-05 20:47:00 Hemadhri root[20856] INFO Done setting up intervals
2024-05-05 20:47:00 Hemadhri root[20856] CRITICAL 2399.76


In [3]:

class Agent:
    def __init__(self, num_of_nodes, _alpha, _gamma):
        self.num_of_nodes = num_of_nodes
        self.num_of_actions = num_of_nodes + 1
        self.alpha = _alpha
        self.gamma = _gamma
        self.q_table = {}

    def sample(self): # choose random node
        return random.randint(0, self.num_of_nodes)

    def get_action(self, curr_state, _explore=False):
        _curr_entry = self.get_q_table_entry(curr_state)
        if _explore:
            _last_node_sorted_index = self.sample()
        else:
            _last_node_sorted_index = np.argmax(self.q_table[_curr_entry][0])
        if _last_node_sorted_index >= self.num_of_nodes:
            _action = -1
        else:
            # 'reverse engineering' the right node for the action (see func get_entry below)
            node_memory_bucket = int(_curr_entry[_last_node_sorted_index])
            _, nodes_memory_view = curr_state
            node_buckets = [self.calc_bucket(memory) for _, memory in nodes_memory_view]
            real_node_index = node_buckets.index(node_memory_bucket)
            _action = nodes_memory_view[real_node_index][0]

        return _curr_entry, _last_node_sorted_index, _action

    def update_q_table(self, _curr_entry, _next_state, _last_node_sorted_index, _reward):
        _next_entry = None
        if self.is_state_in_q_table(_next_state):
            _next_entry = self.get_entry(_next_state)
        _old_value = self.q_table[_curr_entry][0][_last_node_sorted_index]
        next_max = 0 if not _next_entry else max(self.q_table[_next_entry][0])
        _new_value = (1 - self.alpha) * _old_value + self.alpha * (_reward + self.gamma * next_max)
        self.q_table[_curr_entry][0][_last_node_sorted_index] = _new_value
        self.q_table[_curr_entry][1][0] += 1

    def get_entry(self, _state):
        """
        A q-table entry is concatination of sorted node buckets with sorted pod buckets.
        Once a state is converted to an entery, the node for the action needs to be found since the sorting mixed up the order.
        this 'reverse engineering' accurs in the function get_action above
        """
        pod_lookahead_list, nodes_memory_view = _state
        pods_buckets = sorted([str(self.calc_bucket(memory_left)) for _, memory_left in pod_lookahead_list])
        nodes_buckets = sorted([str(self.calc_bucket(memory_left)) for _, memory_left in nodes_memory_view])

        entry_list = nodes_buckets + pods_buckets
        entry = "".join(entry_list)
        return entry

    def get_q_table_entry(self, _state):
        entry = self.get_entry(_state)
        if not self.q_table.get(entry):
            self.q_table[entry] = ([0] * self.num_of_actions, [0])

        return entry

    def is_state_in_q_table(self, _state):
        entry = self.get_entry(_state)
        return self.q_table.get(entry)

    @staticmethod
    def calc_bucket(memory):
        bucket = min(math.floor(round(memory * 100, 0) / PERCENTAGE), NUM_OF_BUCKETS - 1)
        return bucket


class Environment:
    def __init__(self, num_of_nodes=NUM_OF_NODES):
        self.num_of_nodes = num_of_nodes
        self.simulation = None
        self.q_table = None
        self.num_of_actions = None
        self.num_of_pods_lookahead = None
        self.pods_in_nodes = None
        self.node_capacity = None
        self.reset()

    def reset(self, n=NUM_OF_NODES, c=NODE_CAPACITY, p=PODS_LOOKAHEAD):
        self.num_of_nodes = n
        self.node_capacity = c # Capacity - free memory left
        self.pods_in_nodes = [0] * self.num_of_nodes
        self.num_of_pods_lookahead = p
        self.num_of_actions = n + 1
        self.simulation = Cluster(n)

    def start(self, run_time_seconds):
        self.simulation.train_run(run_time_seconds)

    def end(self):
        self.simulation.end_train_run()

    @staticmethod
    def get_state():
        return env.simulation.get_current_state()

    @staticmethod
    def calc_reward_empty_node(_state, overload):
        if overload:
            _reward = -1
        else:
            _reward = 0
            for node in _state[1]:
                if node[1] >= 0.95:
                    _reward += 1
        return _reward

    @staticmethod
    def calc_reward_non_linear(_state, overload, balance_factor=2): 
        """
        For a compact distribution of pods to nodes choose balance_factor = 2
        For a balaced distribution of pods to nodes choose balance_factor = 0.5
        """
        if overload:
            _reward = -1
        else:
            _reward = 0
            for node in _state[1]:
                _reward += (NODE_CAPACITY - node[1]) ** balance_factor

        return _reward


    def step(self, node_choice, reward_func):
        _, overload = self.simulation.schedule_pod(node_choice)
        _next_state = self.simulation.get_current_state()
        # After obtaining _next_state
        #print("_next_state:", _next_state)

        # Accessing pod_scheduled
        pod_scheduled = None
        if _next_state and len(_next_state[0]) > 0:
            pod_scheduled = _next_state[0][0]
        else:
            print("Warning: No pending pods lookahead in _next_state.")
        
        penalty = False
        if node_choice == -1:  # agent chose to do nothing
            for node in _next_state[1]:
                if node[1] > pod_scheduled[1]:
                    penalty = True
                    break
        if penalty:
            # TODO what about bigger lookahead? the penalty might be an overkill
            _reward = -1
        else:
            _reward = reward_func(_next_state, overload)

        _reward *= REWARD_FACTOR

        return _next_state, _reward


In [4]:
env = Environment()
agent = Agent(NUM_OF_NODES, ALPHA, GAMMA)

2024-05-05 20:47:11 Hemadhri root[20856] INFO Initializing cluster...
2024-05-05 20:47:11 Hemadhri root[20856] INFO Cluster config: NUM_OF_NODES=3, NODE_MEMORY=1, SPAWN_TIME_INTERVAL_SECS=0.0001, MAX_NUM_OF_PODS=2399.76, ALPHA=0.3, GAMMA=0.3


In [ ]:

for i in range(1, 2):

    pods_assigned = 0
    env.reset()
    env.start(SECONDS_PER_EPOCH + 1)
    end_time=end_time = dt.datetime.now() + dt.timedelta(seconds=SECONDS_PER_EPOCH)

    while dt.datetime.now() < end_time:
        state = env.get_state(); ''' state = (pending_pods_lookahead, (node_id,nodes_bucket)) '''
        while len(state[0]) < PODS_LOOKAHEAD:
            time.sleep(0.0001)
            state = env.get_state()

        explore = True if random.uniform(0, 1) < EPSILON else False

        curr_entry, last_node_sorted_index, action = agent.get_action(state, explore)

        next_state, reward = env.step(action, env.calc_reward_non_linear)
        agent.update_q_table(curr_entry, next_state, last_node_sorted_index, reward)

        pods_assigned += 1
    env.end()

print("Training finished.\n")

2024-05-05 20:47:19 Hemadhri root[20856] INFO Initializing cluster...
2024-05-05 20:47:19 Hemadhri root[20856] INFO Cluster config: NUM_OF_NODES=3, NODE_MEMORY=1, SPAWN_TIME_INTERVAL_SECS=0.0001, MAX_NUM_OF_PODS=2399.76, ALPHA=0.3, GAMMA=0.3
2024-05-05 20:47:19 Hemadhri root[20856] INFO Run started, running for 361 seconds
2024-05-05 20:47:19 Hemadhri root[20856] INFO Done setting up intervals
2024-05-05 20:47:19 Hemadhri root[20856] INFO Inside schedule pod, with pod ea5261
2024-05-05 20:47:19 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:47:19 Hemadhri root[20856] INFO pod.memory=0.09, node.memory_left=1
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod ea5261 with memory demand 0.09 is scheduled on:
2024-05-05 20:47:19 Hemadhri root[20856] INFO Node 0 with 0.91 memory left
2024-05-05 20:47:19 Hemadhri root[20856] INFO Inside schedule pod, with pod 23641a
2024-05-05 20:47:19 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:47:19 Hemadhri root[20856] INFO pod.memory=0.2, 

2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod d3ebf9 with memory demand 0.18 is scheduled on:
2024-05-05 20:47:19 Hemadhri root[20856] INFO Node 0 with 0.8200000000000001 memory left
2024-05-05 20:47:19 Hemadhri root[20856] INFO Inside schedule pod, with pod 0ea924
2024-05-05 20:47:19 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:47:19 Hemadhri root[20856] INFO pod.memory=0.15, node.memory_left=0.8200000000000001
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod 0ea924 with memory demand 0.15 is scheduled on:
2024-05-05 20:47:19 Hemadhri root[20856] INFO Node 0 with 0.67 memory left
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod d3ebf9 finished
2024-05-05 20:47:19 Hemadhri root[20856] INFO Inside schedule pod, with pod a9866d
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod 0ea924 finished
2024-05-05 20:47:19 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:47:19 Hemadhri root[20856] INFO pod.memory=0.1, node.memory_left=1.0
2024-05-05 20:47:19 Hemadhri root[20856]

2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod f7474f with memory demand 0.23 is scheduled on:
2024-05-05 20:47:19 Hemadhri root[20856] INFO Node 0 with 0.77 memory left
2024-05-05 20:47:19 Hemadhri root[20856] INFO Inside schedule pod, with pod 9a85c0
2024-05-05 20:47:19 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:47:19 Hemadhri root[20856] INFO pod.memory=0.3, node.memory_left=0.77
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod 9a85c0 with memory demand 0.3 is scheduled on:
2024-05-05 20:47:19 Hemadhri root[20856] INFO Node 0 with 0.47000000000000003 memory left
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod 9a85c0 finished
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod f7474f finished
2024-05-05 20:47:19 Hemadhri root[20856] INFO Inside schedule pod, with pod c906e6
2024-05-05 20:47:19 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:47:19 Hemadhri root[20856] INFO pod.memory=0.16, node.memory_left=1.0
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod c906

2024-05-05 20:47:19 Hemadhri root[20856] INFO Node 0 with 0.46 memory left
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod d9bb99 finished
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod 1e2d18 finished
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod 1f0a37 finished


2024-05-05 20:47:19 Hemadhri root[20856] INFO Inside schedule pod, with pod d17713
2024-05-05 20:47:19 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:47:19 Hemadhri root[20856] INFO pod.memory=0.15, node.memory_left=1.0
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod d17713 with memory demand 0.15 is scheduled on:
2024-05-05 20:47:19 Hemadhri root[20856] INFO Node 0 with 0.85 memory left
2024-05-05 20:47:19 Hemadhri root[20856] INFO Inside schedule pod, with pod d2b5a5
2024-05-05 20:47:19 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:47:19 Hemadhri root[20856] INFO pod.memory=0.3, node.memory_left=0.85
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod d2b5a5 with memory demand 0.3 is scheduled on:
2024-05-05 20:47:19 Hemadhri root[20856] INFO Node 0 with 0.55 memory left
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod d2b5a5 finished
2024-05-05 20:47:19 Hemadhri root[20856] INFO Inside schedule pod, with pod 72b2b8
2024-05-05 20:47:19 Hemadhri root[20856] INFO Pod d1

...

2024-05-05 20:51:40 Hemadhri root[20856] INFO Node 0 with 0.9399999999999993 memory left
2024-05-05 20:51:40 Hemadhri root[20856] INFO Inside schedule pod, with pod 75d8e3
2024-05-05 20:51:40 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:51:40 Hemadhri root[20856] INFO pod.memory=0.23, node.memory_left=0.9399999999999993
2024-05-05 20:51:40 Hemadhri root[20856] INFO Pod 75d8e3 with memory demand 0.23 is scheduled on:
2024-05-05 20:51:40 Hemadhri root[20856] INFO Node 0 with 0.7099999999999993 memory left
2024-05-05 20:51:40 Hemadhri root[20856] INFO Pod fe52f6 finished
2024-05-05 20:51:40 Hemadhri root[20856] INFO Pod 75d8e3 finished
2024-05-05 20:51:40 Hemadhri root[20856] INFO Inside schedule pod, with pod f451ea
2024-05-05 20:51:40 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:51:40 Hemadhri root[20856] INFO pod.memory=0.26, node.memory_left=0.9999999999999993
2024-05-05 20:51:40 Hemadhri root[20856] INFO Pod f451ea with memory demand 0.26 is scheduled on:
2024-05-05

2024-05-05 20:51:40 Hemadhri root[20856] INFO Inside schedule pod, with pod bb1de9
2024-05-05 20:51:40 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:51:40 Hemadhri root[20856] INFO pod.memory=0.44, node.memory_left=0.9999999999999993
2024-05-05 20:51:40 Hemadhri root[20856] INFO Pod bb1de9 with memory demand 0.44 is scheduled on:
2024-05-05 20:51:40 Hemadhri root[20856] INFO Node 0 with 0.5599999999999994 memory left
2024-05-05 20:51:40 Hemadhri root[20856] INFO Inside schedule pod, with pod 05c096
2024-05-05 20:51:40 Hemadhri root[20856] INFO node_index: 1
2024-05-05 20:51:40 Hemadhri root[20856] INFO pod.memory=0.24, node.memory_left=1.0000000000000004
2024-05-05 20:51:40 Hemadhri root[20856] INFO Pod 05c096 with memory demand 0.24 is scheduled on:
2024-05-05 20:51:40 Hemadhri root[20856] INFO Node 1 with 0.7600000000000005 memory left
2024-05-05 20:51:40 Hemadhri root[20856] INFO Pod bb1de9 finished
2024-05-05 20:51:40 Hemadhri root[20856] INFO Inside schedule pod, with pod 

2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod 16df7b with memory demand 0.31 is scheduled on:
2024-05-05 20:51:41 Hemadhri root[20856] INFO Node 2 with 0.69 memory left
2024-05-05 20:51:41 Hemadhri root[20856] INFO Inside schedule pod, with pod 6e9ddd
2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod 16df7b finished
2024-05-05 20:51:41 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:51:41 Hemadhri root[20856] INFO pod.memory=0.33, node.memory_left=0.9999999999999993
2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod 6e9ddd with memory demand 0.33 is scheduled on:
2024-05-05 20:51:41 Hemadhri root[20856] INFO Node 0 with 0.6699999999999993 memory left
2024-05-05 20:51:41 Hemadhri root[20856] INFO Inside schedule pod, with pod f26070
2024-05-05 20:51:41 Hemadhri root[20856] INFO node_index: 1
2024-05-05 20:51:41 Hemadhri root[20856] INFO pod.memory=0.3, node.memory_left=1.0000000000000004
2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod f26070 with memory demand 0.3 is schedule

2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod 8911be finished
2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod f26070 finished
2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod 6e9ddd finished
2024-05-05 20:51:41 Hemadhri root[20856] INFO Inside schedule pod, with pod 54ea79
2024-05-05 20:51:41 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:51:41 Hemadhri root[20856] INFO pod.memory=0.12, node.memory_left=0.9999999999999993
2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod 54ea79 with memory demand 0.12 is scheduled on:
2024-05-05 20:51:41 Hemadhri root[20856] INFO Node 0 with 0.8799999999999993 memory left
2024-05-05 20:51:41 Hemadhri root[20856] INFO Inside schedule pod, with pod 970988
2024-05-05 20:51:41 Hemadhri root[20856] INFO node_index: 0
2024-05-05 20:51:41 Hemadhri root[20856] INFO pod.memory=0.22, node.memory_left=0.8799999999999993
2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod 970988 with memory demand 0.22 is scheduled on:
2024-05-05 20:51:41 Hemadhri root

2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod f00e19 finished
2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod 2537ba finished
2024-05-05 20:51:41 Hemadhri root[20856] INFO Pod fb5937 finished
2024-05-05 20:51:41 Hemadhri root[20856] INFO Inside schedule pod, with pod 13b8b6


In [6]:
agent.q_table

{'9990': ([2.383120439688569,
   2.804764436618801,
   2.7460821551081085,
   -98.51802590389823],
  [808]),
 '9992': ([8.258005266782863,
   8.042799320764065,
   9.455131213166784,
   -97.81389722767828],
  [2013]),
 '7991': ([10.135818340627571,
   6.0686056441326475,
   6.164465350733672,
   -96.22027249496954],
  [1795]),
 '7990': ([2.673641371085564,
   4.593451434209801,
   4.315218735324289,
   -97.14236516163547],
  [795]),
 '9991': ([6.246610259017132,
   4.735565490680751,
   4.248883165517329,
   -97.65829666779146],
  [1987]),
 '8991': ([7.999850411616437,
   5.223144591875915,
   4.889035336452981,
   -97.47620082378108],
  [1866]),
 '9993': ([11.87564745449452,
   11.930858389163193,
   15.348044842532733,
   -96.88058051546273],
  [874]),
 '6991': ([10.952483527916755,
   9.712799997696504,
   6.907976027862994,
   -96.8587949433361],
  [892]),
 '7993': ([14.816569093816286,
   12.582681220450572,
   17.157180983452957,
   -94.89206973537658],
  [818]),
 '8992': ([11.41